In [41]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover, SignalStrategy, TrailingStrategy, resample_apply
from backtesting.test import SMA
from backtesting import Backtest

import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import numpy as np
import pandas as pd 
import math as m
import os, glob

In [42]:
import warnings
warnings.filterwarnings("ignore")

In [43]:

WithClassOne = False
CASH = 1000
COMMISSION = 0.0001
MODEL_PATH = 'XGBOOST'#XGBOOST' # 'LSTM'

In [44]:
pwd = os.getcwd()
datasource_path = os.path.join(pwd, r'../../../Results/' + MODEL_PATH + '/')
filenames_models = glob.glob(datasource_path + "/*.csv")
filenames_models.sort()
for file in filenames_models:
    print(filenames_models.index(file), ' ',os.path.basename(file))

0   3C_1D_137F_5137Size_XGBOOST_Class_01_Full.csv
1   3C_1D_137F_5137Size_XGBOOST_Class_01_Test.csv
2   3C_1D_137F_5137Size_XGBOOST_Class_01_Train.csv
3   3C_1D_30F_5137Size_XGBOOST_Class_05_Full.csv
4   3C_1D_62F_5137Size_XGBOOST_Class_01_Full.csv
5   3C_1H_62F_102514Size_XGBOOST_Class_01_Test.csv
6   3C_1H_62F_102514Size_XGBOOST_Class_01_Train.csv
7   3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv
8   3C_1H_62F_22514Size_XGBOOST_Class_01_Train.csv
9   3C_1H_62F_57514Size_XGBOOST_Class_01_Test.csv
10   3C_1H_62F_57514Size_XGBOOST_Class_01_Train.csv
11   5C_1D_14F_5137Size_XGBOOST_Class_01_Full.csv
12   5C_1D_30F_5137Size_XGBOOST_Class_01_Full.csv
13   5C_1D_43F_5137Size_XGBOOST_Class_02_Full.csv


In [45]:
GLOBAL_IDX = 7
NumCLASS =  3


dateparse = lambda x: pd.datetime.strptime(x, '%Y-%m-%d %H:%M:%S')
DATASET = pd.read_csv(filenames_models[GLOBAL_IDX], header=0)
MODEL_NAME = os.path.basename(filenames_models[GLOBAL_IDX])
print(MODEL_NAME)
print(DATASET.head(5))
print(DATASET.shape)


3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv
      Open     High      Low    Close     Volume  Volume_Bid   Spread  \
0  1.10564  1.10569  1.10514  1.10524  3826.7600   3801.2900  0.00003   
1  1.10523  1.10543  1.10492  1.10493  2994.8201   3020.1699  0.00003   
2  1.10491  1.10505  1.10449  1.10492  1548.4700   1332.1300  0.00015   
3  1.10492  1.10521  1.10471  1.10497  1860.4100   1685.1851  0.00009   
4  1.10495  1.10527  1.10488  1.10490  1406.3499   1419.5551  0.00005   

   Pct_Range_Close  Pct_Range_Close_diff           AQV  ...   Trix_15  \
0        -0.000362             -0.000045  2.088313e+09  ...  0.000043   
1        -0.000280              0.000081  2.088316e+09  ...  0.000050   
2        -0.000009              0.000271  2.088317e+09  ...  0.000055   
3         0.000045              0.000054  2.088319e+09  ...  0.000059   
4        -0.000063             -0.000109  2.088321e+09  ...  0.000062   

    Trix_25   Trix_50   Trix_75  MACD_5_25  MACDsign_5_25  MACDdiff_5_25  \


In [46]:
filename = 'BackTesting_Results.csv'
print(filename)
pwd = os.getcwd()
path_backstesting = os.path.join(pwd, r'../../../Results/Backtesting/')
filename_path_backstesting = os.path.join(pwd, r'../../../Results/Backtesting/' + filename)
print(filename_path_backstesting)

BackTesting_Results.csv
/Users/marami3/Documents/ITESO/IDI4/forex_prediction/Jupyter Notebooks/IDI4/backtesting/../../../Results/Backtesting/BackTesting_Results.csv


In [47]:
PRED = True
if NumCLASS == 3:
    if (PRED):
        DATASET['Position'] = DATASET['Predicted_Class']
if NumCLASS == 5:
    if (PRED):
        DATASET['Position'] = DATASET['Predicted_Class']
        if (WithClassOne):
            DATASET.loc[DATASET.Predicted_Class == -2, 'Position'] = -1
            DATASET.loc[DATASET.Predicted_Class == 2, 'Position'] = 1
        else:
            DATASET.loc[DATASET.Predicted_Class == -2, 'Position'] = -1
            DATASET.loc[DATASET.Predicted_Class == 2, 'Position'] = 1
            DATASET.loc[DATASET.Predicted_Class == -1, 'Position'] = 0 # remove Small movements
            DATASET.loc[DATASET.Predicted_Class == 1, 'Position'] = 0 #Remove Small movements
DATASET.head(5)

Open     High      Low    Close     Volume  Volume_Bid   Spread  \
0  1.10564  1.10569  1.10514  1.10524  3826.7600   3801.2900  0.00003   
1  1.10523  1.10543  1.10492  1.10493  2994.8201   3020.1699  0.00003   
2  1.10491  1.10505  1.10449  1.10492  1548.4700   1332.1300  0.00015   
3  1.10492  1.10521  1.10471  1.10497  1860.4100   1685.1851  0.00009   
4  1.10495  1.10527  1.10488  1.10490  1406.3499   1419.5551  0.00005   

   Pct_Range_Close  Pct_Range_Close_diff           AQV  ...   Trix_25  \
0        -0.000362             -0.000045  2.088313e+09  ...  0.000017   
1        -0.000280              0.000081  2.088316e+09  ...  0.000019   
2        -0.000009              0.000271  2.088317e+09  ...  0.000022   
3         0.000045              0.000054  2.088319e+09  ...  0.000024   
4        -0.000063             -0.000109  2.088321e+09  ...  0.000026   

    Trix_50   Trix_75  MACD_5_25  MACDsign_5_25  MACDdiff_5_25  \
0  0.000033  0.000003   0.001242       0.000943       0.000299   
1  0.000033  0.000004   0.001029       0.000960       0.000069   
2  0.000033  0.000005   0.000869       0.000942      -0.000073   
3  0.000033  0.000005   0.000762       0.000906      -0.000144   
4  0.000033  0.000006   0.000658       0.000856      -0.000199   

   Mass_Index_25_8_9  Real_Class  Predicted_Class  Position  
0          24.853139        -1.0              0.0       0.0  
1          24.623666         0.0              0.0       0.0  
2          24.447890         0.0              0.0       0.0  
3          24.299628         0.0              0.0       0.0  
4          24.220745         0.0              0.0       0.0  

[5 rows x 64 columns]

In [48]:
class limits(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    def init(self):
        super().init()
        self.Op_Abierta = False
        
    def next(self):
        sig = self.data.Position[-1]
        if not self.Op_Abierta and sig >= self.buy_lim:
            self.buy()
            self.Op_Abierta = True
        if self.Op_Abierta and sig <= self.sell_lim:
            self.sell()
            self.Op_Abierta = False

In [49]:
class limits2(SignalStrategy, TrailingStrategy):
    buy_lim = 0.99
    sell_lim = -0.99
    
    def init(self):
        super().init()
        
    def next(self):
        sig = self.data.Position[-1]
        if  sig >= self.buy_lim:
            self.buy()
        if  sig <= self.sell_lim:
            self.sell()

In [50]:
class Position(SignalStrategy):
    def init(self):
        global df
        super().init()  
        self.set_signal(self.data.Position)

In [51]:
DATASET['Predicted_Class'].value_counts()

 0.0    2565
 1.0    1269
-1.0     669
Name: Predicted_Class, dtype: int64

In [52]:
DATASET['Real_Class'].value_counts()

 0.0    1934
 1.0    1286
-1.0    1283
Name: Real_Class, dtype: int64

In [53]:
STRATEGY_NAME = limits
print(STRATEGY_NAME.__name__)

limits


In [54]:
bt = Backtest(DATASET, STRATEGY_NAME, cash=CASH, commission=COMMISSION)#trade_on_close=False
bt.run()

Start                               0
End                              4502
Duration                         4502
Exposure [%]                  99.6002
Equity Final [$]              1019.51
Equity Peak [$]               1050.18
Return [%]                    1.95074
Buy & Hold Return [%]        0.573631
Max. Drawdown [%]            -6.62206
Avg. Drawdown [%]           -0.407365
Max. Drawdown Duration           1553
Avg. Drawdown Duration        90.6939
# Trades                          494
Win Rate [%]                  58.2996
Best Trade [%]               0.929498
Worst Trade [%]              -1.84027
Avg. Trade [%]             0.00413353
Max. Trade Duration                99
Avg. Trade Duration           9.07692
Expectancy [%]               0.171954
SQN                          0.309936
Sharpe Ratio                0.0150721
Sortino Ratio               0.0151695
Calmar Ratio              0.000624206
_strategy                      limits
dtype: object

In [55]:
bt.plot()

In [56]:
data = {'Model_Name':[MODEL_NAME], 'PRED':[PRED], 'Strategy_Class':[STRATEGY_NAME.__name__], 'Equity_Final_$':[bt._results['Equity Final [$]']],
       'Equity_Peak_$':[bt._results['Equity Peak [$]']],'Return_%':[bt._results['Return [%]']],'#_Trades':[bt._results['# Trades']],
       'Win_Rate':[bt._results['Win Rate [%]']],'Commission':[COMMISSION],'Cash':[CASH]}
Results = pd.DataFrame(data)
print(Results)

                                      Model_Name  PRED Strategy_Class  \
0  3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv  True         limits   

   Equity_Final_$  Equity_Peak_$  Return_%  #_Trades   Win_Rate  Commission  \
0     1019.507357    1050.184323  1.950736     494.0  58.299595      0.0001   

   Cash  
0  1000  


In [57]:
Results_loaded = pd.read_csv(filename_path_backstesting, header=0)
#print(Results_loaded)

In [58]:
#print(Results)
Results_loaded = Results_loaded.append(Results,ignore_index=True)
print(Results_loaded[-1:])

                                       Model_Name  PRED Strategy_Class  \
41  3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv  True         limits   

    Equity_Final_$  Equity_Peak_$  Return_%  #_Trades   Win_Rate  Commission  \
41     1019.507357    1050.184323  1.950736     494.0  58.299595      0.0001   

    Cash  
41  1000  


In [59]:
Results_loaded.to_csv(filename_path_backstesting, header=True, index=False)

In [60]:
PRED = False

In [61]:
DATASET = pd.read_csv(filenames_models[GLOBAL_IDX], header=0)
MODEL_NAME = os.path.basename(filenames_models[GLOBAL_IDX])
print(MODEL_NAME)
print(DATASET.shape)
print(DATASET.head(5))

3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv
(4503, 63)
      Open     High      Low    Close     Volume  Volume_Bid   Spread  \
0  1.10564  1.10569  1.10514  1.10524  3826.7600   3801.2900  0.00003   
1  1.10523  1.10543  1.10492  1.10493  2994.8201   3020.1699  0.00003   
2  1.10491  1.10505  1.10449  1.10492  1548.4700   1332.1300  0.00015   
3  1.10492  1.10521  1.10471  1.10497  1860.4100   1685.1851  0.00009   
4  1.10495  1.10527  1.10488  1.10490  1406.3499   1419.5551  0.00005   

   Pct_Range_Close  Pct_Range_Close_diff           AQV  ...   Trix_15  \
0        -0.000362             -0.000045  2.088313e+09  ...  0.000043   
1        -0.000280              0.000081  2.088316e+09  ...  0.000050   
2        -0.000009              0.000271  2.088317e+09  ...  0.000055   
3         0.000045              0.000054  2.088319e+09  ...  0.000059   
4        -0.000063             -0.000109  2.088321e+09  ...  0.000062   

    Trix_25   Trix_50   Trix_75  MACD_5_25  MACDsign_5_25  MACDdi

In [62]:
if NumCLASS == 3:
        DATASET['Position'] = DATASET['Real_Class']
if NumCLASS == 5:
        DATASET['Position'] = DATASET['Real_Class']
        if (WithClassOne):
            DATASET.loc[DATASET.Real_Class == -2, 'Position'] = -1
            DATASET.loc[DATASET.Real_Class == 2, 'Position'] = 1
        else:
            DATASET.loc[DATASET.Real_Class == -2, 'Position'] = -1
            DATASET.loc[DATASET.Real_Class == 2, 'Position'] = 1
            DATASET.loc[DATASET.Predicted_Class == -1, 'Position'] = 0 # remove Small movements
            DATASET.loc[DATASET.Predicted_Class == 1, 'Position'] = 0 #Remove Small movements
DATASET.head(10)

Open     High      Low    Close     Volume  Volume_Bid   Spread  \
0  1.10564  1.10569  1.10514  1.10524  3826.7600   3801.2900  0.00003   
1  1.10523  1.10543  1.10492  1.10493  2994.8201   3020.1699  0.00003   
2  1.10491  1.10505  1.10449  1.10492  1548.4700   1332.1300  0.00015   
3  1.10492  1.10521  1.10471  1.10497  1860.4100   1685.1851  0.00009   
4  1.10495  1.10527  1.10488  1.10490  1406.3499   1419.5551  0.00005   
5  1.10490  1.10498  1.10463  1.10472  1583.6100   1987.8000  0.00003   
6  1.10474  1.10474  1.10428  1.10431  3935.5801   3755.8701  0.00004   
7  1.10431  1.10472  1.10419  1.10432  4779.9399   5164.3901  0.00004   
8  1.10431  1.10472  1.10406  1.10458  3041.2600   2697.3301  0.00004   
9  1.10458  1.10465  1.10430  1.10442  2465.9900   1878.3199  0.00001   

   Pct_Range_Close  Pct_Range_Close_diff           AQV  ...   Trix_25  \
0        -0.000362             -0.000045  2.088313e+09  ...  0.000017   
1        -0.000280              0.000081  2.088316e+09  ...  0.000019   
2        -0.000009              0.000271  2.088317e+09  ...  0.000022   
3         0.000045              0.000054  2.088319e+09  ...  0.000024   
4        -0.000063             -0.000109  2.088321e+09  ...  0.000026   
5        -0.000163             -0.000100  2.088322e+09  ...  0.000028   
6        -0.000371             -0.000208  2.088326e+09  ...  0.000029   
7         0.000009              0.000380  2.088331e+09  ...  0.000030   
8         0.000235              0.000226  2.088334e+09  ...  0.000030   
9        -0.000145             -0.000380  2.088336e+09  ...  0.000031   

    Trix_50   Trix_75  MACD_5_25  MACDsign_5_25  MACDdiff_5_25  \
0  0.000033  0.000003   0.001242       0.000943       0.000299   
1  0.000033  0.000004   0.001029       0.000960       0.000069   
2  0.000033  0.000005   0.000869       0.000942      -0.000073   
3  0.000033  0.000005   0.000762       0.000906      -0.000144   
4  0.000033  0.000006   0.000658       0.000856      -0.000199   
5  0.000034  0.000006   0.000531       0.000791      -0.000260   
6  0.000034  0.000007   0.000334       0.000700      -0.000366   
7  0.000034  0.000007   0.000207       0.000601      -0.000394   
8  0.000034  0.000008   0.000190       0.000519      -0.000329   
9  0.000034  0.000008   0.000134       0.000442      -0.000308   

   Mass_Index_25_8_9  Real_Class  Predicted_Class  Position  
0          24.853139        -1.0              0.0      -1.0  
1          24.623666         0.0              0.0       0.0  
2          24.447890         0.0              0.0       0.0  
3          24.299628         0.0              0.0       0.0  
4          24.220745         0.0              0.0       0.0  
5          24.152520        -1.0              0.0      -1.0  
6          24.108628         0.0              0.0       0.0  
7          24.035687         0.0              0.0       0.0  
8          23.895990         0.0              0.0       0.0  
9          23.824414         0.0              0.0       0.0  

[10 rows x 64 columns]

In [63]:
bt = Backtest(DATASET, STRATEGY_NAME, cash=CASH, commission=COMMISSION)#trade_on_close=False
bt.run()

Start                             0
End                            4502
Duration                       4502
Exposure [%]                99.6224
Equity Final [$]            9265.17
Equity Peak [$]             9265.17
Return [%]                  826.517
Buy & Hold Return [%]      0.573631
Max. Drawdown [%]         -0.598539
Avg. Drawdown [%]        -0.0224204
Max. Drawdown Duration           17
Avg. Drawdown Duration      3.08837
# Trades                       1330
Win Rate [%]                97.3684
Best Trade [%]              1.71998
Worst Trade [%]           -0.325976
Avg. Trade [%]             0.167326
Max. Trade Duration              23
Avg. Trade Duration         3.37218
Expectancy [%]             0.168932
SQN                         23.8571
Sharpe Ratio               0.837007
Sortino Ratio               2.90718
Calmar Ratio               0.279557
_strategy                    limits
dtype: object

In [64]:
bt.plot()

In [65]:
data = {'Model_Name':[MODEL_NAME], 'PRED':[PRED], 'Strategy_Class':[STRATEGY_NAME.__name__], 'Equity_Final_$':[bt._results['Equity Final [$]']],
       'Equity_Peak_$':[bt._results['Equity Peak [$]']],'Return_%':[bt._results['Return [%]']],'#_Trades':[bt._results['# Trades']],
       'Win_Rate':[bt._results['Win Rate [%]']],'Commission':[COMMISSION],'Cash':[CASH]}
Results = pd.DataFrame(data)
print(Results)

filename = 'BackTesting_Results.csv'
print(filename)
pwd = os.getcwd()
datasource_path_results = os.path.join(pwd, r'../../../Results/Backtesting/')
filename_path = os.path.join(pwd, r'../../../Results/Backtesting/' + filename)
print(filename_path)

                                      Model_Name   PRED Strategy_Class  \
0  3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv  False         limits   

   Equity_Final_$  Equity_Peak_$   Return_%  #_Trades   Win_Rate  Commission  \
0     9265.166502    9265.166502  826.51665    1330.0  97.368421      0.0001   

   Cash  
0  1000  
BackTesting_Results.csv
/Users/marami3/Documents/ITESO/IDI4/forex_prediction/Jupyter Notebooks/IDI4/backtesting/../../../Results/Backtesting/BackTesting_Results.csv


In [66]:
Results_loaded = pd.read_csv(filename_path_backstesting, header=0)

In [67]:
#print(Results)
Results_loaded = Results_loaded.append(Results,ignore_index=True)
print(Results_loaded[-2:])

                                       Model_Name   PRED Strategy_Class  \
41  3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv   True         limits   
42  3C_1H_62F_22514Size_XGBOOST_Class_01_Test.csv  False         limits   

    Equity_Final_$  Equity_Peak_$    Return_%  #_Trades   Win_Rate  \
41     1019.507357    1050.184323    1.950736     494.0  58.299595   
42     9265.166502    9265.166502  826.516650    1330.0  97.368421   

    Commission  Cash  
41      0.0001  1000  
42      0.0001  1000  


In [68]:
Results_loaded.to_csv(filename_path, header=True, index=False)